<a href="https://colab.research.google.com/github/ponchakridsrisuwan/clean_data_with_R/blob/main/clean_data_with_R.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
install.packages("tidyverse")
install.packages("RSQLite")
install.packages("glue")
install.packages("lubridate")

Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)

also installing the dependencies ‘textshaping’, ‘conflicted’, ‘jsonlite’, ‘ragg’


Warning message in install.packages("tidyverse"):
“installation of package ‘textshaping’ had non-zero exit status”
Warning message in install.packages("tidyverse"):
“installation of package ‘ragg’ had non-zero exit status”
Warning message in install.packages("tidyverse"):
“installation of package ‘tidyverse’ had non-zero exit status”
Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)

also installing the dependency ‘plogr’


Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)

Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)



In [ ]:
library(tidyverse)
library(RSQLite)
library(glue)
library(lubridate)

── Attaching packages ─────────────────────────────────────── tidyverse 1.3.1 ──

✔ ggplot2 3.4.2     ✔ purrr   1.0.1
✔ tibble  3.2.1     ✔ dplyr   1.1.2
✔ tidyr   1.3.0     ✔ stringr 1.5.0
✔ readr   2.1.4     ✔ forcats 1.0.0

── Conflicts ────────────────────────────────────────── tidyverse_conflicts() ──
✖ dplyr::filter() masks stats::filter()
✖ dplyr::lag()    masks stats::lag()


Attaching package: ‘lubridate’


The following objects are masked from ‘package:base’:

    date, intersect, setdiff, union




In [ ]:
from google.colab import drive
drive.mount('/content/drive')

# csv1

In [ ]:
df1 <- read.csv('/content/drive/MyDrive/dataset/salary_survey-1.csv')
head(df1)

Timestamp          How.old.are.you. What.industry.do.you.work.in.
1 4/24/2019 11:43:21 35-44            Government                   
2 4/24/2019 11:43:26 25-34            Environmental nonprofit      
3 4/24/2019 11:43:27 18-24            Market Research              
4 4/24/2019 11:43:27 25-34            Biotechnology                
5 4/24/2019 11:43:29 25-34            Healthcare                   
6 4/24/2019 11:43:29 25-34            Information Management       
  Job.title                                What.is.your.annual.salary.
1 Talent Management Asst. Director         75000                      
2 Operations Director                      65,000                     
3 Market Research Assistant                36,330                     
4 Senior Scientist                         34600                      
5 Social worker (embedded in primary care) 55000                      
6 Associate Consultant                     45,000                     
  Please.indicate.the.currency Where.are.you.located...City.state.country.
1 USD                          Nashville, TN                              
2 USD                          Madison, Wi                                
3 USD                          Las Vegas, NV                              
4 GBP                          Cardiff, UK                                
5 USD                          Southeast Michigan, USA                    
6 USD                          Seattle, WA                                
  How.many.years.of.post.college.professional.work.experience.do.you.have.
1 11 - 20 years                                                           
2 8 - 10 years                                                            
3 2 - 4 years                                                             
4 5-7 years                                                               
5 5-7 years                                                               
6 8 - 10 years                                                            
  If.your.job.title.needs.additional.context..please.clarify.here.
1                                                                 
2                                                                 
3                                                                 
4                                                                 
5                                                                 
6                                                                 
  If..Other...please.indicate.the.currency.here..
1                                                
2                                                
3                                                
4                                                
5                                                
6

In [ ]:
sele_df1 <- df1[, c(4, 5, 6, 7, 8)]
colnames(sele_df1) <- c("job", "salary", "currency", "address", "w_experience")

In [ ]:
head(sele_df1)

job                                      salary currency
1 Talent Management Asst. Director         75000  USD     
2 Operations Director                      65,000 USD     
3 Market Research Assistant                36,330 USD     
4 Senior Scientist                         34600  GBP     
5 Social worker (embedded in primary care) 55000  USD     
6 Associate Consultant                     45,000 USD     
  address                 w_experience 
1 Nashville, TN           11 - 20 years
2 Madison, Wi             8 - 10 years 
3 Las Vegas, NV           2 - 4 years  
4 Cardiff, UK             5-7 years    
5 Southeast Michigan, USA 5-7 years    
6 Seattle, WA             8 - 10 years

In [ ]:
sele_df1$salary <- as.numeric(gsub(",", "", sele_df1$salary))

Warning message in eval(expr, envir, enclos):
“NAs introduced by coercion”


In [ ]:
head(filter(sele_df1,! currency == "USD"))

job                           salary currency address                
1 Senior Scientist              34600  GBP      Cardiff, UK            
2 Marketing Manager                NA  CAD      Montreal, QC, Canada   
3 Senior research executive     30000  GBP      London, UK             
4 communiity investment officer 68000  CAD      ottawa, ontario, canada
5 Visual Effects Compositor     50000  CAD      Toronto/ON/Canada      
6 convention coordinator           NA  CAD                             
  w_experience 
1 5-7 years    
2 8 - 10 years 
3 5-7 years    
4 8 - 10 years 
5 2 - 4 years  
6 11 - 20 years

In [ ]:
sele_df1 %>%
  group_by(currency) %>%
  summarise(count = n())

currency count
1  AUD/NZD    668
2  CAD       1708
3  CHF         36
4  EUR        506
5  GBP       1010
6  HKD         15
7  JPY         34
8  Other      189
9  SEK         28
10 USD      30164
11 ZAR         16

In [ ]:
library(dplyr)

In [ ]:
exchange_rates <- c(
  AUD = 0.74,
  NZD = 0.69,
  CAD = 0.81,
  CHF = 0.92,
  EUR = 1.12,
  GBP = 1.37,
  HKD = 0.13,
  JPY = 0.0091,
  SEK = 0.11,
  USD = 1,
  ZAR = 0.069
)

In [ ]:
convert_to_usd <- function(salary, currency) {
  exchange_rate <- exchange_rates[currency]
  if (is.na(exchange_rate)) {
    warning(paste("Exchange rate for", currency, "not found. Salary not converted."))
    return(salary)
  }
  converted_salary <- salary / exchange_rate
  return(converted_salary)
}

In [ ]:
sele_df1 <- sele_df1 %>%
  rowwise() %>%
  mutate(salary_usd = convert_to_usd(salary, currency)) %>%
  ungroup()

Warning message:
“There were 857 warnings in `mutate()`.
The first warning was:
ℹ In argument: `salary_usd = convert_to_usd(salary, currency)`.
ℹ In row 243.
Caused by warning in `convert_to_usd()`:
! Exchange rate for Other not found. Salary not converted.
ℹ Run `dplyr::last_dplyr_warnings()` to see the 856 remaining warnings.”


In [ ]:
head(sele_df1)

job                                      salary currency
1 Talent Management Asst. Director         75000  USD     
2 Operations Director                      65000  USD     
3 Market Research Assistant                36330  USD     
4 Senior Scientist                         34600  GBP     
5 Social worker (embedded in primary care) 55000  USD     
6 Associate Consultant                     45000  USD     
  address                 w_experience  salary_usd
1 Nashville, TN           11 - 20 years 75000.00  
2 Madison, Wi             8 - 10 years  65000.00  
3 Las Vegas, NV           2 - 4 years   36330.00  
4 Cardiff, UK             5-7 years     25255.47  
5 Southeast Michigan, USA 5-7 years     55000.00  
6 Seattle, WA             8 - 10 years  45000.00

In [ ]:
sele_df1$job <- trimws(sele_df1$job)

In [ ]:
head(sele_df1)

job                                      salary currency
1 Talent Management Asst. Director         75000  USD     
2 Operations Director                      65000  USD     
3 Market Research Assistant                36330  USD     
4 Senior Scientist                         34600  GBP     
5 Social worker (embedded in primary care) 55000  USD     
6 Associate Consultant                     45000  USD     
  address                 w_experience  salary_usd
1 Nashville, TN           11 - 20 years 75000.00  
2 Madison, Wi             8 - 10 years  65000.00  
3 Las Vegas, NV           2 - 4 years   36330.00  
4 Cardiff, UK             5-7 years     25255.47  
5 Southeast Michigan, USA 5-7 years     55000.00  
6 Seattle, WA             8 - 10 years  45000.00

In [ ]:
sele_df1$job <- tolower(sele_df1$job)

In [ ]:
sele_df1

job                                        salary currency
1     talent management asst. director            75000 USD     
2     operations director                         65000 USD     
3     market research assistant                   36330 USD     
4     senior scientist                            34600 GBP     
5     social worker (embedded in primary care)    55000 USD     
6     associate consultant                        45000 USD     
7     development manager                         51000 USD     
8     student records coordinator                 54371 USD     
9     director                                    45000 USD     
10    copywriter                                  80000 USD     
11    office manager                              72000 USD     
12    hr and administrative coordinator           50000 USD     
13    marketing manager                              NA CAD     
14    senior research executive                   30000 GBP     
15    teacher                                     54000 USD     
16    senior consultant                              NA USD     
17    associate professor                         52000 USD     
18    communiity investment officer               68000 CAD     
19    visual effects compositor                   50000 CAD     
20    senior marketing manager                    90000 USD     
21    assistant media editor                         NA USD     
22    assistant director of development research     NA USD     
23    public services coordinator                 50000 USD     
24    instructional consultant                    58000 USD     
25    event producer                              70000 USD     
26    support qa lead                             71000 USD     
27    associate governmental program analyst      60000 USD     
28    convention coordinator                         NA CAD     
29    pet sitter                                     NA USD     
30    senior research scientist                  106000 USD     
⋮     ⋮                                          ⋮      ⋮       
34345 client manager                              52000 USD     
34346 accounting specialist                       45680 USD     
34347 coordinator                                 60000 USD     
34348 sde                                         23300 USD     
34349 maintenance engineer                        27000 GBP     
34350 project coordinator                         57000 USD     
34351 associate dean                              70000 USD     
34352 content marketing specialist                35000 USD     
34353 teacher (hs)                                80000 USD     
34354 it manager                                  86000 USD     
34355 executive assistant                         50000 USD     
34356 executive assistant                         50000 USD     
34357 production manager                          60000 USD     
34358 consultant                                  60000 USD     
34359 estimator                                   50000 CAD     
34360 administrative business partner             73000 USD     
34361 senior game developer                       98000 USD     
34362 lead scientist                             117000 USD     
34363 project architect                              NA USD     
34364 engineer                                    76000 USD     
34365 account executive                          130000 USD     
34366 support helpdesk analyst                    39520 USD     
34367 implementation consultant                   55000 USD     
34368 instructuonal coach                         80000 USD     
34369 partner                                    175000 USD     
34370 pharmacist                                 163000 USD     
34371 support tech                                   35 USD     
34372 director                                   300000 CAD     
34373 analist                                    160000 Other   
34374 senior data strategist             

In [ ]:
sele_df_edit <- sele_df1

In [ ]:
sele_df_edit$salary <- NULL
sele_df_edit$currency <- NULL

In [ ]:
sele_df_edit$w_experience <- gsub(" ", "", sele_df_edit$w_experience)
head(sele_df_edit)

job                                      address                 w_experience
1 talent management asst. director         Nashville, TN           11-20years  
2 operations director                      Madison, Wi             8-10years   
3 market research assistant                Las Vegas, NV           2-4years    
4 senior scientist                         Cardiff, UK             5-7years    
5 social worker (embedded in primary care) Southeast Michigan, USA 5-7years    
6 associate consultant                     Seattle, WA             8-10years   
  salary_usd
1 75000.00  
2 65000.00  
3 36330.00  
4 25255.47  
5 55000.00  
6 45000.00

In [ ]:
sele_df_edit$w_experience <- gsub("[^0-9-]", "", sele_df_edit$w_experience)
head(sele_df_edit)

job                                      address                 w_experience
1 talent management asst. director         Nashville, TN           11-20       
2 operations director                      Madison, Wi             8-10        
3 market research assistant                Las Vegas, NV           2-4         
4 senior scientist                         Cardiff, UK             5-7         
5 social worker (embedded in primary care) Southeast Michigan, USA 5-7         
6 associate consultant                     Seattle, WA             8-10        
  salary_usd
1 75000.00  
2 65000.00  
3 36330.00  
4 25255.47  
5 55000.00  
6 45000.00

In [ ]:
sele_df_edit$address

[1] "Nashville, TN"                                                                                         
    [2] "Madison, Wi"                                                                                           
    [3] "Las Vegas, NV"                                                                                         
    [4] "Cardiff, UK"                                                                                           
    [5] "Southeast Michigan, USA"                                                                               
    [6] "Seattle, WA"                                                                                           
    [7] "Dallas, Texas, United States"                                                                          
    [8] "Philadelphia"                                                                                          
    [9] "Bridgeport, mi. Usa"                                                                                   
   [10] "DC"                                                                                                    
   [11] "Brick NJ"                                                                                              
   [12] "Baltimore, Maryland, USA"                                                                              
   [13] "Montreal, QC, Canada"                                                                                  
   [14] "London, UK"                                                                                            
   [15] "Geirgia"                                                                                               
   [16] "New Jersey, USA"                                                                                       
   [17] "Pittsburgh/PA/USA"                                                                                     
   [18] "ottawa, ontario, canada"                                                                               
   [19] "Toronto/ON/Canada"                                                                                     
   [20] "Washington, DC"                                                                                        
   [21] "New York, NY, USA"                                                                                     
   [22] "Boston, MA, USA"                                                                                       
   [23] "MA, USA"                                                                                               
   [24] "Wisconsin, U.S."                                                                                       
   [25] "Berkeley, CA, USA"                                                                                     
   [26] "Maryland"                                                                                              
   [27] "Sacramento, CA USA"                                                                                    
   [28] ""                                                                                                      
   [29] "Pittsburgh, PA"                                                                                        
   [30] "Hampton Roads, VA, USA"                                                                                
   [31] "Milwaukee, Wisconsin USA"                                                                              
   [32] "Miami"                                                                                                 
   [33] "San Francisco/CA/USA"                                                                                  
   [34] "Virginia, United States"                                                                               
   [35] "Washington, DC"                                                                                        
   [36] "Boston, MA, United States of America"   

In [ ]:
sele_df_edit$address <- gsub("/", ",", sele_df_edit$address)
sele_df_edit$address <- tolower(sele_df_edit$address)
sele_df_edit$address <- str_trim(sele_df_edit$address)
sele_df_edit$address <- str_replace_all(sele_df_edit$address, ",", " ")
sele_df_edit$address <- str_remove_all(sele_df_edit$address, "[./]")

In [ ]:
# sele_df_edit$address <- str_replace_all(sele_df_edit$address, "usa", ",usa")
# sele_df_edit$address <- str_replace_all(sele_df_edit$address, "united states", ",usa")
# sele_df_edit$address <- str_replace_all(sele_df_edit$address, "u.s.", ",usa")
# sele_df_edit$address <- str_replace_all(sele_df_edit$address, "germany", ",de")
# sele_df_edit$address <- str_replace_all(sele_df_edit$address, "canada", ",ca")
# sele_df_edit$address <- str_replace_all(sele_df_edit$address, "united kingdom", ",uk")
# sele_df_edit$address <- str_replace_all(sele_df_edit$address, "singapore", ",sg")


In [ ]:
# สร้างคู่ key-value ของชื่อเต็มและตัวย่อของประเทศ
country_names <- c(
  "afghanistan" = "af",
  "albania" = "al",
  "algeria" = "dz",
  "andorra" = "ad",
  "angola" = "ao",
  "antigua and barbuda" = "ag",
  "argentina" = "ar",
  "armenia" = "am",
  "australia" = "au",
  "austria" = "at",
  "azerbaijan" = "az",
  "bahamas" = "bs",
  "bahrain" = "bh",
  "bangladesh" = "bd",
  "barbados" = "bb",
  "belarus" = "by",
  "belgium" = "be",
  "belize" = "bz",
  "benin" = "bj",
  "bhutan" = "bt",
  "bolivia" = "bo",
  "bosnia and herzegovina" = "ba",
  "botswana" = "bw",
  "brazil" = "br",
  "brunei" = "bn",
  "bulgaria" = "bg",
  "burkina faso" = "bf",
  "burundi" = "bi",
  "cabo verde" = "cv",
  "cambodia" = "kh",
  "cameroon" = "cm",
  "canada" = "ca",
  "central african republic" = "cf",
  "chad" = "td",
  "chile" = "cl",
  "china" = "cn",
  "colombia" = "co",
  "comoros" = "km",
  "congo" = "cg",
  "costa rica" = "cr",
  "croatia" = "hr",
  "cuba" = "cu",
  "cyprus" = "cy",
  "czech republic" = "cz",
  "denmark" = "dk",
  "djibouti" = "dj",
  "dominica" = "dm",
  "dominican republic" = "do",
  "east timor" = "tl",
  "ecuador" = "ec",
  "egypt" = "eg",
  "el salvador" = "sv",
  "equatorial guinea" = "gq",
  "eritrea" = "er",
  "estonia" = "ee",
  "eswatini" = "sz",
  "ethiopia" = "et",
  "fiji" = "fj",
  "finland" = "fi",
  "france" = "fr",
  "gabon" = "ga",
  "gambia" = "gm",
  "georgia" = "ge",
  "germany" = "de",
  "ghana" = "gh",
  "greece" = "gr",
  "grenada" = "gd",
  "guatemala" = "gt",
  "guinea" = "gn",
  "guinea-bissau" = "gw",
  "guyana" = "gy",
  "haiti" = "ht",
  "honduras" = "hn",
  "hungary" = "hu",
  "iceland" = "is",
  "india" = "in",
  "indonesia" = "id",
  "iran" = "ir",
  "iraq" = "iq",
  "ireland" = "ie",
  "israel" = "il",
  "italy" = "it",
  "jamaica" = "jm",
  "japan" = "jp",
  "jordan" = "jo",
  "kazakhstan" = "kz",
  "kenya" = "ke",
  "kiribati" = "ki",
  "korea, north" = "kp",
  "korea, south" = "kr",
  "kosovo" = "xk",
  "kuwait" = "kw",
  "kyrgyzstan" = "kg",
  "laos" = "la",
  "latvia" = "lv",
  "lebanon" = "lb",
  "lesotho" = "ls",
  "liberia" = "lr",
  "libya" = "ly",
  "liechtenstein" = "li",
  "lithuania" = "lt",
  "luxembourg" = "lu",
  "madagascar" = "mg",
  "malawi" = "mw",
  "malaysia" = "my",
  "maldives" = "mv",
  "mali" = "ml",
  "malta" = "mt",
  "marshall islands" = "mh",
  "mauritania" = "mr",
  "mauritius" = "mu",
  "mexico" = "mx",
  "micronesia" = "fm",
  "moldova" = "md",
  "monaco" = "mc",
  "mongolia" = "mn",
  "montenegro" = "me",
  "morocco" = "ma",
  "mozambique" = "mz",
  "myanmar" = "mm",
  "namibia" = "na",
  "nauru" = "nr",
  "nepal" = "np",
  "netherlands" = "nl",
  "new zealand" = "nz",
  "nicaragua" = "ni",
  "niger" = "ne",
  "nigeria" = "ng",
  "north macedonia" = "mk",
  "norway" = "no",
  "oman" = "om",
  "pakistan" = "pk",
  "palau" = "pw",
  "panama" = "pa",
  "papua new guinea" = "pg",
  "paraguay" = "py",
  "peru" = "pe",
  "philippines" = "ph",
  "poland" = "pl",
  "portugal" = "pt",
  "qatar" = "qa",
  "romania" = "ro",
  "russia" = "ru",
  "rwanda" = "rw",
  "saint kitts and nevis" = "kn",
  "saint lucia" = "lc",
  "saint vincent and the grenadines" = "vc",
  "samoa" = "ws",
  "san marino" = "sm",
  "sao tome and principe" = "st",
  "saudi arabia" = "sa",
  "senegal" = "sn",
  "serbia" = "rs",
  "seychelles" = "sc",
  "sierra leone" = "sl",
  "singapore" = "sg",
  "slovakia" = "sk",
  "slovenia" = "si",
  "solomon islands" = "sb",
  "somalia" = "so",
  "south africa" = "za",
  "south sudan" = "ss",
  "spain" = "es",
  "sri lanka" = "lk",
  "sudan" = "sd",
  "suriname" = "sr",
  "sweden" = "se",
  "switzerland" = "ch",
  "syria" = "sy",
  "taiwan" = "tw",
  "tajikistan" = "tj",
  "tanzania" = "tz",
  "thailand" = "th",
  "togo" = "tg",
  "tonga" = "to",
  "trinidad and tobago" = "tt",
  "tunisia" = "tn",
  "turkey" = "tr",
  "turkmenistan" = "tm",
  "tuvalu" = "tv",
  "uganda" = "ug",
  "ukraine" = "ua",
  "united arab emirates" = "ae",
  "united kingdom" = "gb",
  "united states" = "usa",
  "uruguay" = "uy",
  "uzbekistan" = "uz",
  "vanuatu" = "vu",
  "vatican city" = "va",
  "venezuela" = "ve",
  "vietnam" = "vn",
  "yemen" = "ye",
  "zambia" = "zm",
  "zimbabwe" = "zw"
)


In [ ]:
for (country in names(country_names)) {
  sele_df_edit$address <- str_replace_all(sele_df_edit$address, country, paste0(",", country_names[country]))
}

In [ ]:
colSums(is.na(sele_df_edit))

job      address w_experience   salary_usd 
           0            0            0         3617

In [ ]:
sele_df_edit$job <- str_replace_all(sele_df_edit$job, "asst", "assistant")
head(sele_df_edit)

job                                      address                 w_experience
1 talent management assistant. director    nashville  tn           11-20       
2 operations director                      madison  wi             8-10        
3 market research assistant                las vegas  nv           2-4         
4 senior scientist                         cardiff  uk             5-7         
5 social worker (embedded in primary care) southeast michigan  usa 5-7         
6 associate consultant                     seattle  wa             8-10        
  salary_usd
1 75000.00  
2 65000.00  
3 36330.00  
4 25255.47  
5 55000.00  
6 45000.00

In [ ]:
sele_df_edit

job                                        address                   
1     talent management assistant. director      nashville  tn             
2     operations director                        madison  wi               
3     market research assistant                  las vegas  nv             
4     senior scientist                           cardiff  uk               
5     social worker (embedded in primary care)   southeast michigan  usa   
6     associate consultant                       seattle  wa               
7     development manager                        dallas  texas  ,usa       
8     student records coordinator                philadelphia              
9     director                                   bridgeport  mi usa        
10    copywriter                                 dc                        
11    office manager                             brick nj                  
12    hr and administrative coordinator          baltimore  maryland  usa  
13    marketing manager                          montreal  qc  ,ca         
14    senior research executive                  london  uk                
15    teacher                                    geirgia                   
16    senior consultant                          new jersey  usa           
17    associate professor                        pittsburgh pa usa         
18    communiity investment officer              ottawa  ontario  ,ca      
19    visual effects compositor                  toronto on ,ca            
20    senior marketing manager                   washington  dc            
21    assistant media editor                     new york  ny  usa         
22    assistant director of development research boston  ma  usa           
23    public services coordinator                ma  usa                   
24    instructional consultant                   wisconsin  us             
25    event producer                             berkeley  ca  usa         
26    support qa lead                            maryland                  
27    associate governmental program analyst     sacramento  ca usa        
28    convention coordinator                                               
29    pet sitter                                 pittsburgh  pa            
30    senior research scientist                  hampton roads  va  usa    
⋮     ⋮                                          ⋮                         
34345 client manager                             louisville ky usa         
34346 accounting specialist                      mpls  mn  usa             
34347 coordinator                                los angeles  ca           
34348 sde                                                                  
34349 maintenance engineer                       ,gb                       
34350 project coordinator                        nashville  tn  usa        
34351 associate dean                             ,usa                      
34352 content marketing specialist               charlotte  nc             
34353 teacher (hs)                               tulare ca usa             
34354 it manager                                 san antonio  texas  usa   
34355 executive assistant                        montgomery  al isa        
34356 executive assistant                        montgomery  al isa        
34357 production manager                         boston  ma usa            
34358 consultant                                 graham  wa                
34359 estimator                                  ,ca                       
34360 administrative business partner            san jose  california usa  
34361 senior game developer                      raleigh  nc usa           
34362 lead scientist                             denver  colorado          
34363 project architect                          portland  oregon  usa     
34364 engineer                                   minneapolis  minnesota    
34365 account executive                          new y

# CSV2

In [ ]:
df2 <- read.csv('/content/drive/MyDrive/dataset/salary_survey-2.csv')
head(df2)

Timestamp         Employment.Type Company.Name    Company.Size.....Employees
1                                                                             
2 9/11/2019 0:47:40 Full-time       Citi            10,000-100,000            
3 9/11/2019 0:51:26 Full-time       Ibm             10,000-100,000            
4 9/11/2019 0:51:56 Full-time       No Answer       10,000-100,000            
5 9/11/2019 0:52:28 Full-time       Td ameritrade   1,000-10,000              
6 9/11/2019 0:54:02 Full-time       The Table Times 20-100                    
  Primary.Location..Country. Primary.Location..City. Industry.in.Company       
1                                                                              
2 United States (US)         Manhattan               Finance                   
3 United States (US)                                 Software                  
4 Australia (AU)                                     General Engineering       
5 United States (US)         Ann arbor               Web Development           
6 United States (US)         Portland                Media - Print & Journalism
  Public.or.Private.Company Years.Experience.in.Industry
1                                                       
2 Public                    10-20                       
3 Public                    10-20                       
4 Public                    5-10                        
5 Public                    2-5                         
6 Private                   5-10                        
  Years.of.Experience.in.Current.Company ⋯
1                                        ⋯
2 2-5                                    ⋯
3 10-20                                  ⋯
4 2-5                                    ⋯
5 0-2                                    ⋯
6 2-5                                    ⋯
  Total.Bonus.in.2018..cumulative.annual.value.in.USD.
1    NA                                               
2 40000                                               
3 22000                                               
4    NA                                               
5 21000                                               
6     0                                               
  Total.Stock.Options.Equity.in.2018..cumulative.annual.value.in.USD.
1 NA                                                                 
2  0                                                                 
3  0                                                                 
4 NA                                                                 
5 NA                                                                 
6  0                                                                 
  Health.Insurance.Offered Annual.Vacation..in.Weeks.
1                                                    
2 Yes                      4                         
3 Yes                      5                         
4 N/A                      4                         
5 Yes                      3                         
6 No                       1                         
  Are.you.happy.at.your.current.position.
1                                        
2 It's Complicated                       
3 No                                     
4 Yes                                    
5 Yes                                    
6 It's Complicated                       
  Do.you.plan.to.resign.in.the.next.12.months.
1                                             
2 Yes                                         
3 No                                          
4 No                                          
5 No                                          
6 Don't know                                  
  What.are.your.thoughts.about.the.direction.of.your.industry.                                                                                                    
1                                                                                                                                                     

In [ ]:
sele_df1 <- df1[, c(4, 5, 6, 7, 8)]
colnames(sele_df1) <- c("job", "salary", "currency", "address", "w_experience")